In [2]:
#constants and other necessary stuff
import sys
!{sys.executable} -m pip install plotly

import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy import constants

a0 = constants.physical_constants['Bohr radius'][0]
Angstrom = constants.angstrom

In [3]:
def r_phi_theta(x, y, z):
    r = np.sqrt(x**2 + y**2 + z**2)
    phi = np.arctan2(y, x) + np.pi
    theta = np.arccos(z/r)
    return r, phi, theta

In [4]:
X, Y, Z = np.mgrid[-20*a0:20*a0:48j, -20*a0:20*a0:48j, -20*a0:20*a0:48j]
r_grid, phi_grid, theta_grid = r_phi_theta(X, Y, Z)

In [5]:
def probfunc(r, wavefunc):
    p = r**2 * np.conj(wavefunc) * wavefunc
    return p.real / np.max(p.real)
# The .real syntax picks off the real part of a complex number. Even though the
# imaginary part of the probability is zero, variable p is still represented in
# the computer as a complex number. Our plotting routines will only work on
# arrays of real numbers.

In [6]:
n1l0m0 = lambda r: np.exp(-r/a0) / (np.sqrt(np.pi) * a0**1.5)

n2l0m0 = lambda r: (2 - r/a0) * np.exp(-r/(2*a0)) / (4 * np.sqrt(2*np.pi) * a0**1.5)

These don't depend on phi or theta because I believe their plotted function looks spherical. Because it's perfectly spherical, it doesn't matter what phi or theta you choose, only the radius R.

It looks like the n1l0m0 probability function is more centrally condensed compared to the n2l0m0 probability function.

Also, the slice from the n1l0m0 probability function matches my expectation for the hydrogen atom in the ground state, as it shows that the probability function is spherically symmetrical.

The main difference from the n=1 and n=2 slices are that for n=1, the probability is completely spherically symmetrical, while the n=2 slice shows an inner ring or circle where the probability drops down, showing a place close to the nucleus where the electron is not likely to be.

Below, I will plot the n=3, l=2, m=2  probability function.

In [16]:
n3l2m2 = lambda r, phi, theta: (r**2/a0**2) * np.exp(-r/(3*a0)) * (np.sin(theta))**2 * \
                               np.exp(2j * phi) / (162 * np.sqrt(np.pi) * a0**1.5)

In [17]:
prob_n3l2m2 = probfunc(r_grid, n3l2m2(r_grid, phi_grid, theta_grid))

In [19]:
# n = 3, l = 2, m = 2
prob_n3l2m2 = probfunc(r_grid, n3l2m2(r_grid, phi_grid, theta_grid))

fig = go.Figure(data=go.Isosurface(
    x=X.flatten() / Angstrom, # x values of the grid in Angstroms
    y=Y.flatten() / Angstrom, # y values of the grid in Angstroms
    z=Z.flatten() / Angstrom, # z values of the grid in Angstroms
    value=prob_n3l2m2.flatten(), # independent variable
    isomin=0.05, # Minimum normalized probability density to render in an isosurface
    isomax=0.95, # Maximum normalized probability density to render in an isosurface
    opacity=0.4, # Set a low opacity so each surface is partially transparent
    colorscale='Plotly3_r', # Nice-looking color table
    surface_count=8, # number of isosurfaces to plot (2 by default: only min and max)
    colorbar_nticks=8, # colorbar ticks correspond to isosurface values
    caps=dict(x_show=False, y_show=False, z_show=False),
    slices_x=dict(show=True, locations=[0]),
    ))

# Change axis lables and make the plot larger than the default
fig.update_layout(scene = dict(
                    xaxis_title='x (Angstroms)',
                    yaxis_title='y (Angstroms)',
                    zaxis_title='z (Angstroms)'),
                    width=700,
                    margin=dict(r=10, b=10, l=10, t=10))

fig.show()